In [1]:
import os
from src.video_preprocessing.download_videos.youtube_download import preprocess_video
from src.video_preprocessing.scene_detection.scene_detect import detect_scenes
from src.video_preprocessing.scene_detection.ocr import extract_text_from_slide
from src.video_preprocessing.download_videos.download_utils import (
    transcribe_audio_files,
    extract_and_store_audio,
    transcription_to_text,
    create_metadata,
)
from src.ocr.pytesseract_image_to_text import extract_text_from_image
from src.llm.ollama_implementation.ollama_experiment import (
    prompt_llm_summary,
    generate_caption_using_llava,
    prompt_llm_extensive_summary,
)
from transformers import CLIPProcessor, CLIPModel, CLIPTokenizer
from PIL import Image

import torch
import pandas as pd
import time
from loguru import logger
import pickle

2024-06-13 23:35:30.951 | INFO     | src.ocr.pytesseract_image_to_text:<module>:20 - Extracted text: Lecture overview

1 R programming basics

1. Get 2 Data wrangling
3 Tidy data
2. Look 4 Low dimensional visualization
5 High dimensi i
3. Conclude 7 Empirical Statistical Assessment

8 Analytical Statistical Assessment
9 Statistical Assessment for Big Data
Case Study
10 Linear regression
11 Classification
12 Supervised Learning

Julien Gagneur Graphically supported hypotheses 3/70




# Download Pipeline
Download a video from a specific URL on YouTube, then run:
- Scene detection
- Keyframe detection

The resulting data will be stored under `/data/raw/<NAME>`

In [ ]:
# Define options and input for downloading a video from youtube

# INSERT video name here
name = "biology_chapter_3_3"
# INSERT video URL here
url = "https://youtu.be/DZSEErNZ1d4?si=f6YxKQ9rP6iqgTfk"
# INSERT chunk length in seconds 30s --> 30, no splitting: None
chunks = None


opts_aud = {"format": "mp3/bestaudio/best", "keep-video": True}
opts_vid = {"format": "mp4/bestvideo/best"}

In [ ]:
# Downloads the video creates the relevant datafolders and transcribes the video
data_path = preprocess_video(
    download=True,
    uploaded_vid="ignore",  # path to local file
    url=url,
    name=name,
    aud_opts=opts_aud,
    vid_opts=opts_vid,  # Video download settings
    audio_file=name + ".mp3",
    input_file=name + ".mp4",
    output="output.mp4",
    split_length=chunks,
)

In [ ]:
#  Now that we have downloaded the video we want to perform scene_Detection:
detect_scenes(data_path)

In [ ]:
# Extract the audio per detected scene
extract_and_store_audio(
    os.path.join(data_path, "scene_snippets"),
    os.path.join(data_path, "audio_chunks"),
)

# Audio Transcription using Whisper

For Faster Inference Please Use Tiny!

In [ ]:
# Transcribe the different snippets snippets:
audio_dir = os.path.join(data_path, "audio_chunks")
transcriptions_dir = os.path.join(data_path, "transcriptions")

model_type = "tiny"  # change to 'large' if you want more accurate results,
# change to 'medium.en' or 'large.en' for all english language tasks,
# and change to 'small' or 'base' for faster inference
lang = "en"

# Run whisper on all .wav files in audio_dir
transcribe_audio_files(audio_dir, transcriptions_dir, model_type=model_type, lang=lang)

# Starting the Analysis of the Information Contained in the Video

### Inputs

* **Transcriptions**: [insert description or link to transcription]
* **Extraction from Slides using OCR**: [insert description or link to extracted content]
* **Textual Interpretation of Visual Information using LLAVA**: [insert description or link to 
interpreted information]

In [2]:
import json
import tqdm

image_path = "/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes"

# Transform transcription file

keyframes = {}

for filename in tqdm.tqdm(os.listdir(image_path)):
    # Check if the file ends with the specified extension
    if filename.endswith(".jpg"):
        filepath = os.path.join(image_path, filename)
        keyframe_num = int(filename.split("-")[2])

        # Extract text using OCR:
        ocr_extracted_text = extract_text_from_image(filepath)
        # logger.info(f"OCR_results: {ocr_extracted_text}")

        transcription_file_path = os.path.join(
            os.path.dirname(image_path),
            "transcriptions",
            filename.replace("-01.jpg", ".csv"),
        )

        transcription, timestamps = transcription_to_text(transcription_file_path)
        logger.info(f"Transcription_text: {transcription}")

        # Extract textual understanding of Visual features using LLAVA:

        # llava_results = generate_caption_using_llava(filepath)
        # logger.info(f"LLava_results: {llava_results}")

        # clip_llm_summary = prompt_llm_summary(
        #     slide_content=ocr_extracted_text,
        #     transcription=transcription,
        #     llava_output=llava_results,
        # )

        # extensive_summary = prompt_llm_extensive_summary(
        #     slide_content=ocr_extracted_text,
        #     transcription=transcription,
        #     llava_output=llava_results,
        # )

        # Alternative that goes faster.
        llava_results = "llava_results"
        clip_llm_summary = "clip_llm_summary"
        extensive_summary = "extensive_summary"

        keyframe, keyframe_metadata = create_metadata(
            keyframe_num,
            filepath,
            timestamps,
            transcription,
            ocr_extracted_text,
            llava_results,
            clip_llm_summary,
            extensive_summary,
        )
        keyframes[keyframe] = keyframe_metadata
        print(keyframes)

    # Save keyframes dictionary as Pickle

# Save with pickle
with open("data.pickle", "wb") as file:
    pickle.dump(keyframes, file)

  1%|          | 1/113 [00:00<00:43,  2.57it/s]

{15: {'img_path': '/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes/biology_chapter_3_3-Scene-015-01.jpg', 'timestamps': [0, 84], 'transcription': " While we can survive without food for several weeks, survival without water is limited  just a few days.  When you haven't had enough water, you get dehydrated.  dehydration is decreased water intake.  You might even start feeling symptoms when you haven't had enough water.  Rainer symptoms include muscle cramps, fatigue, headache, dizziness, nausea, confusion,  and even an increased heart rate.  That last one is due to a decreased blood volume when you're dehydrated so your heart  tries to compensate for that effect by speeding up as it tries to maintain homeostasis.  When you're severely dehydrated, things like hallucinations, heat stroke, and even death  can result.  One of the major ways that you lose water is through sweating.  It's the evaporation of water from the skin and it helps to cool t

2024-06-13 23:35:32.498 | INFO     | __main__:<module>:27 - Transcription_text:  The cell membranes job is very important.  Besides being the boundary from the external and internal environment of the cell,  it determines what materials will be allowed in or out of the cell.  It's semi-permable, meaning some molecules are able to cross  and those that can't are prevented from crossing.
  2%|▏         | 2/113 [00:00<00:39,  2.78it/s]

{15: {'img_path': '/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes/biology_chapter_3_3-Scene-015-01.jpg', 'timestamps': [0, 84], 'transcription': " While we can survive without food for several weeks, survival without water is limited  just a few days.  When you haven't had enough water, you get dehydrated.  dehydration is decreased water intake.  You might even start feeling symptoms when you haven't had enough water.  Rainer symptoms include muscle cramps, fatigue, headache, dizziness, nausea, confusion,  and even an increased heart rate.  That last one is due to a decreased blood volume when you're dehydrated so your heart  tries to compensate for that effect by speeding up as it tries to maintain homeostasis.  When you're severely dehydrated, things like hallucinations, heat stroke, and even death  can result.  One of the major ways that you lose water is through sweating.  It's the evaporation of water from the skin and it helps to cool t

2024-06-13 23:35:32.862 | INFO     | __main__:<module>:27 - Transcription_text:  are going to let's find only implant cells.  The answer is chloroplasts.  How about a bonus question what process occurs in chloroplasts?  The answer to that is photosynthesis.
  3%|▎         | 3/113 [00:01<00:39,  2.76it/s]

...

{15: {'img_path': '/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes/biology_chapter_3_3-Scene-015-01.jpg', 'timestamps': [0, 84], 'transcription': " While we can survive without food for several weeks, survival without water is limited  just a few days.  When you haven't had enough water, you get dehydrated.  dehydration is decreased water intake.  You might even start feeling symptoms when you haven't had enough water.  Rainer symptoms include muscle cramps, fatigue, headache, dizziness, nausea, confusion,  and even an increased heart rate.  That last one is due to a decreased blood volume when you're dehydrated so your heart  tries to compensate for that effect by speeding up as it tries to maintain homeostasis.  When you're severely dehydrated, things like hallucinations, heat stroke, and even death  can result.  One of the major ways that you lose water is through sweating.  It's the evaporation of water from the skin and it helps to cool t

2024-06-13 23:36:19.997 | INFO     | __main__:<module>:27 - Transcription_text:  In our last chapter, we discussed the structural composition of proteins.  Remember the repeating subunit or monomer unit that proteins are made from are called amino acids  and that there's about 20 different amino acids that make up the proteins that are in our body.  The DNA codes for those amino acids to be chained in the right order and then other cell components  will fold those chains of amino acids into just the right shape so those proteins can do  the job that they need to do.  From what you eat, your body is actually able to synthesize or assemble many of the commonly  occurring amino acids that our proteins are made out of.  There are some, however, out of those 20 amino acids that our bodies cannot synthesize  on their own.  These are called essential amino acids.  You must get these by eating the proper foods.
 99%|█████████▉| 112/113 [00:48<00:00,  1.91it/s]

{15: {'img_path': '/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes/biology_chapter_3_3-Scene-015-01.jpg', 'timestamps': [0, 84], 'transcription': " While we can survive without food for several weeks, survival without water is limited  just a few days.  When you haven't had enough water, you get dehydrated.  dehydration is decreased water intake.  You might even start feeling symptoms when you haven't had enough water.  Rainer symptoms include muscle cramps, fatigue, headache, dizziness, nausea, confusion,  and even an increased heart rate.  That last one is due to a decreased blood volume when you're dehydrated so your heart  tries to compensate for that effect by speeding up as it tries to maintain homeostasis.  When you're severely dehydrated, things like hallucinations, heat stroke, and even death  can result.  One of the major ways that you lose water is through sweating.  It's the evaporation of water from the skin and it helps to cool t

2024-06-13 23:36:20.472 | INFO     | __main__:<module>:27 - Transcription_text:  Unfortunately, this process creates something called trans fats.  They're produced by incomplete hydrogenation, which also changes the structure of the fatty acid  tails in the fats so that even though there is mostly carbon-carbon double bonds, the fatty acids  are flat and not caked. For our bodies, these fats are not required.  Nor are they beneficial. In fact, researchers indicated they're very unhealthy.  If you choose to eat energy bars, protein bars, fiber bars and other nutrition bars,  it's best to look for those that do not contain trans fats.  There's health risks of consuming those foods that have trans fats in them.  They include clogged arteries, heart disease and increased risk of diabetes.
100%|██████████| 113/113 [00:48<00:00,  2.32it/s]

{15: {'img_path': '/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes/biology_chapter_3_3-Scene-015-01.jpg', 'timestamps': [0, 84], 'transcription': " While we can survive without food for several weeks, survival without water is limited  just a few days.  When you haven't had enough water, you get dehydrated.  dehydration is decreased water intake.  You might even start feeling symptoms when you haven't had enough water.  Rainer symptoms include muscle cramps, fatigue, headache, dizziness, nausea, confusion,  and even an increased heart rate.  That last one is due to a decreased blood volume when you're dehydrated so your heart  tries to compensate for that effect by speeding up as it tries to maintain homeostasis.  When you're severely dehydrated, things like hallucinations, heat stroke, and even death  can result.  One of the major ways that you lose water is through sweating.  It's the evaporation of water from the skin and it helps to cool t

In [ ]:
# Assuming keyframes is your dictionary
keyframes_count = len(keyframes)
print("Number of keyframes:", keyframes_count)

In [ ]:
def get_model_info(model_ID, device):
    # Save the model to device
    model = CLIPModel.from_pretrained(model_ID).to(device)
    # Get the processor
    processor = CLIPProcessor.from_pretrained(model_ID)
    # Get the tokenizer
    tokenizer = CLIPTokenizer.from_pretrained(model_ID)
    # Return model, processor & tokenizer
    return model, processor, tokenizer


# Set the device
device = "cuda" if torch.cuda.is_available() else "cpu"
# Define the model ID
model_ID = "openai/clip-vit-base-patch32"
# Get model, processor & tokenizer
model, processor, tokenizer = get_model_info(model_ID, device)


def get_image(image_path):
    image = Image.open(image_path)
    # Convert the image to RGB
    rgb_image = image.convert("RGB")
    return rgb_image


def get_single_image_embedding(text, my_image, processor, model, device):
    image = processor(text=text, images=my_image, return_tensors="pt")[
        "pixel_values"
    ].to(device)
    embedding = model.get_image_features(image)
    # convert the embeddings to numpy array
    return embedding.cpu().detach().numpy()


one_image = get_image(
    image_path="/Users/magic-rabbit/Documents/AFM/afm-vlm/data/raw/biology_chapter_3_3/extracted_keyframes/biology_chapter_3_3-Scene-055-01.jpg"
)


one_vector = get_single_image_embedding(
    response, one_image, processor, model, device
)  # Simple test

In [ ]:
# Generated one embedding?

print(one_vector)